## Game Recommendation System with Vector Search

In [1]:
from langchain_community.document_loaders import TextLoader
from langchain_text_splitters import CharacterTextSplitter
from langchain_openai import OpenAIEmbeddings
from langchain_chroma import Chroma

In [2]:
from dotenv import load_dotenv

load_dotenv()

True

In [3]:
import pandas as pd

games = pd.read_csv('../data/processed/games_cleaned.csv')
games.head()

app_id                   name release_date  peak_ccu  required_age  price  \
0    20200       Galactic Bowling   2008-10-21         0             0  19.99   
1   655370           Train Bandit   2017-10-12         0             0   0.99   
2  1732930           Jolt Project   2021-11-17         0             0   4.99   
3  1355720               Henosis™   2020-07-23         0             0   5.99   
4  1139950  Two Weeks in Painland   2020-02-03         0             0   0.00   

   dlc_count                                     about_the_game  \
0          0  Galactic Bowling is an exaggerated and stylize...   
1          0  THE LAW!! Looks to be a showdown atop a train....   
2          0  Jolt Project: The army now has a new robotics ...   
3          0  HENOSIS™ is a mysterious 2D Platform Puzzler w...   
4          0  ABOUT THE GAME Play as a hacker who has arrang...   

                                 supported_languages full_audio_languages  \
0                                        ['English']                   []   
1  ['English', 'French', 'Italian', 'German', 'Sp...                   []   
2                 ['English', 'Portuguese - Brazil']                   []   
3  ['English', 'French', 'Italian', 'German', 'Sp...                   []   
4                     ['English', 'Spanish - Spain']                   []   

   ...  median_playtime_forever  median_playtime_two_weeks  \
0  ...                        0                          0   
1  ...                        0                          0   
2  ...                        0                          0   
3  ...                        0                          0   
4  ...                        0                          0   

              developers             publishers  \
0  Perpetual FX Creative  Perpetual FX Creative   
1           Rusty Moyher           Wild Rooster   
2          Campião Games          Campião Games   
3      Odd Critter Games      Odd Critter Games   
4          Unusual Games          Unusual Games   

                                          categories  \
0  ['Single-player', 'Multi-player', 'Steam Achie...   
1  ['Single-player', 'Steam Achievements', 'Full ...   
2                                  ['Single-player']   
3       ['Single-player', 'Full controller support']   
4            ['Single-player', 'Steam Achievements']   

                                         genres  \
0                 ['Casual', 'Indie', 'Sports']   
1                           ['Action', 'Indie']   
2  ['Action', 'Adventure', 'Indie', 'Strategy']   
3              ['Adventure', 'Casual', 'Indie']   
4                        ['Adventure', 'Indie']   

                                                tags  estimated_owners_min  \
0           ['Indie', 'Casual', 'Sports', 'Bowling']                     0   
1  ['Indie', 'Action', 'Pixel Graphics', '2D', 'R...                     0   
2                                               ['']                     0   
3  ['2D Platformer', 'Atmospheric', 'Surreal', 'M...                     0   
4  ['Indie', 'Adventure', 'Nudity', 'Violent', 'S...                     0   

   estimated_owners_max                                       tagged_about  
0                 20000  20200 Galactic Bowling is an exaggerated and s...  
1                 20000  655370 THE LAW!! Looks to be a showdown atop a...  
2                 20000  1732930 Jolt Project: The army now has a new r...  
3                 20000  1355720 HENOSIS™ is a mysterious 2D Platform P...  
4                 20000  1139950 ABOUT THE GAME Play as a hacker who ha...  

[5 rows x 31 columns]

In [4]:
games['tagged_about'].to_csv(
    '../data/processed/tagged_about.txt',
    sep='\n',
    index=False,
    header=False
)

In [5]:
raw_documents = TextLoader('../data/processed/tagged_about.txt').load()
text_splitter = CharacterTextSplitter(chunk_size=0, chunk_overlap=0, separator='\n')
documents = text_splitter.split_documents(raw_documents)

Created a chunk of size 1049, which is longer than the specified 0
Created a chunk of size 498, which is longer than the specified 0
Created a chunk of size 636, which is longer than the specified 0
Created a chunk of size 623, which is longer than the specified 0
Created a chunk of size 680, which is longer than the specified 0
Created a chunk of size 1843, which is longer than the specified 0
Created a chunk of size 794, which is longer than the specified 0
Created a chunk of size 699, which is longer than the specified 0
Created a chunk of size 990, which is longer than the specified 0
Created a chunk of size 1376, which is longer than the specified 0
Created a chunk of size 2425, which is longer than the specified 0
Created a chunk of size 2086, which is longer than the specified 0
Created a chunk of size 664, which is longer than the specified 0
Created a chunk of size 1245, which is longer than the specified 0
Created a chunk of size 1726, which is longer than the specified 0
Cre

In [6]:
# Commenting out to avoid re-embedding and extra OpenAI API costs.
# Embeddings are already stored in '../data/chroma_storage'.

# stored in '../data/chroma_storage', so we can simply load them instead.
# db_games = Chroma.from_documents(
#     documents,
#     embedding=OpenAIEmbeddings(),
#     persist_directory='../data/chroma_storage'
# )

In [7]:
db_games = Chroma(
    persist_directory="../data/chroma_storage",  
    embedding_function=OpenAIEmbeddings()
)

print("✅ Chroma DB loaded successfully!")

✅ Chroma DB loaded successfully!


In [8]:
def semantic_game_rec(query: str, top_k: int = 10) -> pd.DataFrame:
    """
    Retrieve the top-k most similar games based on a semantic search query.

    Parameters
    ----------
    query : str
        The input search query.
    top_k : int, optional
        The number of top similar games to retrieve (default is 10).

    Returns
    -------
    pd.DataFrame
        A DataFrame containing the recommended games with matching `app_id`s.
    """
    recs = db_games.similarity_search(query=query, k=top_k)
    game_ids = [int(recs[i].page_content.split()[0]) for i in range(len(recs))]
    game_recs = games[games['app_id'].isin(game_ids)]
    
    return game_recs

In [14]:
semantic_game_rec('A game related to nature and animals')

app_id                                               name  \
1146   1779710                               SEARCH ALL - ANIMALS   
4729    922700  Hidden Animals: Photo Hunt. Seek and Find Obje...   
17146  1296810                 Naturalealia: Forest Determination   
19623  1036200                                       Song Animals   
24881   906160                          Repeat the image: Animals   
37331  1428150                                             SAVAGE   
42293  1028590                                          The WILDS   
57745  1260340                                 Naturalist Stories   
59626  1923720                   Wildlife Planet: The Incremental   
83306  1733110                                   Of Life and Land   

      release_date  peak_ccu  required_age  price  dlc_count  \
1146    2021-10-19         1             0   0.99          0   
4729    2018-10-18         2             0   2.99          0   
17146   2020-05-22         0             0   6.99          0   
19623   2019-03-25         0             0   0.00          1   
24881   2018-08-04         0             0   3.99          1   
37331   2020-12-21         0             0   0.99          0   
42293   2022-02-15         1             0   9.99          0   
57745   2020-08-02         0             0   9.99          0   
59626   2022-08-25        37             0   2.69          0   
83306   2024-04-02       130             0  22.49          1   

                                          about_the_game  \
1146   SEARCH ALL - ANIMALS is a game in the genre of...   
4729   Discover what it feels like to be a wildlife p...   
17146  Based on 1930's cartoon style made with hand-d...   
19623  Song Animals is a short adventure puzzle game,...   
24881  Repeat the image: Animals - is a game for very...   
37331  This is an adventure game in the wild. You can...   
42293  Prepare to enter The WILDS! Become the animal ...   
57745  We move on the planet with great speed and do ...   
59626  Tired and exhausted from your daily life? You ...   
83306  Take the role of a leader delegated to build n...   

                                     supported_languages  \
1146   ['English', 'French', 'Italian', 'German', 'Sp...   
4729   ['English', 'French', 'Italian', 'German', 'Sp...   
17146                                        ['English']   
19623                                        ['English']   
24881                                        ['English']   
37331  ['English', 'French', 'German', 'Spanish - Spa...   
42293                                        ['English']   
57745                             ['English', 'Russian']   
59626  ['English', 'French', 'German', 'Korean', 'Sim...   
83306  ['English', 'German', 'French', 'Italian', 'Sp...   

                                    full_audio_languages  ...  \
1146   ['English', 'French', 'Italian', 'German', 'Sp...  ...   
4729                                                  []  ...   
17146                                                 []  ...   
19623                                                 []  ...   
24881                                        ['English']  ...   
37331                                                 []  ...   
42293                                                 []  ...   
57745                                                 []  ...   
59626                                                 []  ...   
83306                                                 []  ...   

       median_playtime_forever  median_playtime_two_weeks  \
1146                         0                          0   
4729                         0                          0   
17146                        0                          0   
19623                        0                          0   
24881                        0                          0   
37331                        0                          0   
42293                        0                          0   
57745            